In [1]:
from instance_reader import read_instance
from heuristics import greedy_wave_selection
from Low_levels import *
import random

from funciones_auxiliares import seleccionar_segun_probabilidad

# instancia

In [2]:
instance = read_instance("datasets/a/instance_0002.txt")

# Low Levels

In [3]:
low_level1 = LowLevel1_agregacion(id=1, nombre= "LowLevel1")
low_level2 = LowLevel2_agregacion(id=2, nombre= "LowLevel2")
low_level3 = LowLevel1_eliminacion(id=3, nombre= "LowLevel3")
low_level4 = LowLevel2_eliminacion(id=4, nombre= "LowLevel4")
low_level5 = LowLevel1_swap(id=5, nombre= "LowLevel5")
low_level6 = LowLevel2_swap(id=6, nombre= "LowLevel6")
low_level7 = LowLevel3_swap(id=7, nombre= "LowLevel7")
low_level8 = LowLevel3_agregacion(id=8, nombre= "LowLevel8")
low_level9 = LowLevel1_factibilizadora(id=9, nombre="LowLevel9")
low_level10 = LowLevel2_factibilizadora(id=10, nombre="LowLevel10")

# Definimos una lista de niveles bajos

low_levels = [low_level1, low_level2,low_level3, low_level4, low_level5,
              low_level6, low_level7, low_level8, low_level9, low_level10]

In [4]:
solucion_inicial_2 = instance.constructora2()
solucion_inicial_2.diversity_runners

[0, 1, 2, 3]

In [5]:
solucion_inicial_2.total_units_order

2

In [6]:
solucion_inicial_2.total_units_runner

214

In [7]:
low_level8 = LowLevel3_agregacion(id=1, nombre= "LowLevel1")

In [8]:
sol_2 = low_level8.implementacion(solucion_inicial_2)

In [9]:
sol_2.objective_value

5.0

In [10]:
ordenes_fuera = list(set(instance.orders)-set(solucion_inicial_2.selected_orders))


In [14]:
epocs = 100000
solucion_inicial_2 = instance.constructora2()

V = 0.5

n = len(low_levels)

h = 10

P = np.ones((n, n))
T = np.zeros((n, n))

Q = np.ones((n, 2))
S = np.zeros((n, 2))

# inicializamos la matriz T_ij con P_ij / sum_{k in low_levels} P_ik
for i in range(n):
    suma_P = sum(P[i])
    suma_Q = sum(Q[i])
    T[i] = P[i] / suma_P
    S[i] = Q[i] / suma_Q

solucion_inicial = solucion_inicial_2 #Se comienza con una solución inicial s^c
mejor_solucion = solucion_inicial_2 #Se comienza con una mejor solución s*

secuencia = [] #Se inicia una secuencia vacía
matriz_secuencias = []

i_last = random.choice(low_levels)

sum_epocs = 0

soluciones_factibles = []
costo_inicial = solucion_inicial.objective_value - solucion_inicial.costo_infactible()
costo_mejor_solucion = mejor_solucion.objective_value - mejor_solucion.costo_infactible()

print(mejor_solucion.objective_value)
for count in range(epocs):
    id_i_next = seleccionar_segun_probabilidad(T[i_last.id-1]) #Setea la siguiente low_level
    i_next = low_levels[id_i_next]
    secuencia.append(id_i_next) #Agrega la siguiente low level a la lista
    u_next = random.choices([0,1], weights=S[i_next.id-1], k=1)[0] #Entrega u = 0 o 1 con probabilidad S_{i_next, u}
    
    if u_next == 1:
        solucion_temporal = i_next.implementacion(solucion_inicial) #Implementamos la low-level siguiente
        costo_temporal = solucion_temporal.objective_value - solucion_temporal.costo_infactible()
        
        if mejor_solucion.is_factible: #Calculo de threshold según factibilidad de mejor solución
            rho = 10**-5 + V*(1-len(secuencia)/epocs)
        else:
            rho = 10**-3
        
        if costo_temporal > costo_inicial or costo_temporal > (1+rho)*costo_mejor_solucion: #Condición para considerar la solución temporal como inicial
            solucion_inicial = solucion_temporal
            costo_inicial = costo_temporal
            
        if costo_temporal>costo_mejor_solucion: #Condición para considerar la solución temporal como mejor solución
            mejor_solucion = solucion_temporal
            costo_mejor_solucion = costo_temporal
            if mejor_solucion.is_factible:
                soluciones_factibles.append(mejor_solucion)
             #Actualizar la matriz P y S
            Q[secuencia[-1], 1] =  Q[secuencia[-1], 1] + 1
            for i in range(len(secuencia)-1):
                i_k = secuencia[i]
                i_k_1 = secuencia[i+1]
                P[i_k, i_k_1] = P[i_k, i_k_1]+1
                Q[i_k, 0] = Q[i_k, 0]+1
                for i in range(n):
                    suma_P = sum(P[i])
                    suma_Q = sum(Q[i])
                    T[i] = P[i] / suma_P
                    S[i] = Q[i] / suma_Q
        print(f"epoc: {count}, secuencia = {secuencia}, s_t = {solucion_temporal.objective_value} {solucion_temporal.is_factible}, s_c = {solucion_inicial.objective_value} {solucion_inicial.is_factible}, s* = {mejor_solucion.objective_value} {mejor_solucion.is_factible}")
        secuencia = []
    i_last = i_next
    
print(mejor_solucion)
        

1.0
epoc: 0, secuencia = [1], s_t = 1.5 False, s_c = 1.0 True, s* = 1.0 True
epoc: 1, secuencia = [5], s_t = 1.0 False, s_c = 1.0 True, s* = 1.0 True
epoc: 2, secuencia = [2], s_t = 2.0 False, s_c = 1.0 True, s* = 1.0 True
epoc: 3, secuencia = [0], s_t = 1.0 True, s_c = 1.0 True, s* = 1.0 True
epoc: 5, secuencia = [8, 0], s_t = 1.0 True, s_c = 1.0 True, s* = 1.0 True
epoc: 6, secuencia = [8], s_t = 1.0 True, s_c = 1.0 True, s* = 1.0 True
epoc: 7, secuencia = [6], s_t = 1.5 False, s_c = 1.0 True, s* = 1.0 True
epoc: 16, secuencia = [7, 9, 3, 0, 5, 9, 0, 3, 8], s_t = 1.0 True, s_c = 1.0 True, s* = 1.0 True
epoc: 18, secuencia = [2, 3], s_t = 2.0 False, s_c = 1.0 True, s* = 1.0 True
epoc: 21, secuencia = [7, 1, 9], s_t = 1.0 True, s_c = 1.0 True, s* = 1.0 True
epoc: 26, secuencia = [5, 2, 7, 5, 0], s_t = 1.0 True, s_c = 1.0 True, s* = 1.0 True
epoc: 28, secuencia = [5, 6], s_t = 1.5 False, s_c = 1.0 True, s* = 1.0 True
epoc: 29, secuencia = [5], s_t = 1.0 False, s_c = 1.0 True, s* = 1.0 T

In [ ]:
epocs = 100000
solucion_inicial_2 = instance.constructora2()

V = 0.5

n = len(low_levels)

h = 10

P = np.ones((n, n))
T = np.zeros((n, n))

Q = np.ones((n, 2))
S = np.zeros((n, 2))

# inicializamos la matriz T_ij con P_ij / sum_{k in low_levels} P_ik
for i in range(n):
    suma_P = sum(P[i])
    suma_Q = sum(Q[i])
    T[i] = P[i] / suma_P
    S[i] = Q[i] / suma_Q

solucion_inicial = solucion_inicial_2 #Se comienza con una solución inicial s^c
mejor_solucion = solucion_inicial_2 #Se comienza con una mejor solución s*

secuencia = [] #Se inicia una secuencia vacía
matriz_secuencias = []

i_last = random.choice(low_levels)

sum_epocs = 0

soluciones_factibles = []
costo_inicial = solucion_inicial.objective_value - solucion_inicial.costo_infactible()
costo_mejor_solucion = mejor_solucion.objective_value - mejor_solucion.costo_infactible()

print(mejor_solucion.objective_value)
for count in range(epocs):
    id_i_next = seleccionar_segun_probabilidad(T[i_last.id-1]) #Setea la siguiente low_level
    i_next = low_levels[id_i_next]
    secuencia.append(id_i_next) #Agrega la siguiente low level a la lista
    u_next = random.choices([0,1], weights=S[i_next.id-1], k=1)[0] #Entrega u = 0 o 1 con probabilidad S_{i_next, u}
    
    if u_next == 1:
        solucion_temporal = i_next.implementacion(solucion_inicial) #Implementamos la low-level siguiente
        costo_temporal = solucion_temporal.objective_value - solucion_temporal.costo_infactible()
        
        if mejor_solucion.is_factible: #Calculo de threshold según factibilidad de mejor solución
            rho = 10**-5 + V*(1-len(secuencia)/epocs)
        else:
            rho = 10**-3
            
        #Castigamos el freno si me da infactible
        if not solucion_temporal.is_factible:
            Q[secuencia[-1],1] = 0.7*Q[secuencia[-1],1]
            S[secuencia[-1]] = Q[secuencia[-1]]/sum(Q[secuencia[-1]])
        
        if costo_temporal > costo_inicial: #Condición para considerar la solución temporal como inicial
            solucion_inicial = solucion_temporal
            costo_inicial = costo_temporal
            
        if costo_temporal > (1+rho)*costo_mejor_solucion: #Condición para considerar la solución temporal como mejor solución
            mejor_solucion = solucion_temporal
            costo_mejor_solucion = costo_temporal
            if mejor_solucion.is_factible:
                soluciones_factibles.append(mejor_solucion)
             #Actualizar la matriz P y S
            Q[secuencia[-1], 1] =  Q[secuencia[-1], 1] + 1
            for i in range(len(secuencia)-1):
                i_k = secuencia[i]
                i_k_1 = secuencia[i+1]
                P[i_k, i_k_1] = P[i_k, i_k_1]+1
                Q[i_k, 0] = Q[i_k, 0]+1
                for i in range(n):
                    suma_P = sum(P[i])
                    suma_Q = sum(Q[i])
                    T[i] = P[i] / suma_P
                    S[i] = Q[i] / suma_Q
        print(f"epoc: {count}, secuencia = {secuencia}, s_t = {solucion_temporal.objective_value} {solucion_temporal.is_factible}, s_c = {solucion_inicial.objective_value} {solucion_inicial.is_factible}, s* = {mejor_solucion.objective_value} {mejor_solucion.is_factible}")
        secuencia = []
    i_last = i_next
    
print(mejor_solucion)
        

array([[0.5, 0.5],
       [0.5, 0.5],
       [0.5, 0.5],
       [0.5, 0.5],
       [0.5, 0.5],
       [0.5, 0.5],
       [0.5, 0.5],
       [0.5, 0.5]])

In [21]:
mejor_solucion = None
best_value = 0
epocs = 10000

solucion_inicial_1 = instance.constructora1()
solucion_inicial_2 = instance.constructora2()
P_ij = np.ones((len(low_levels), len(low_levels)))
T_ij = np.zeros((len(low_levels), len(low_levels)))


# inicializamos la matriz T_ij con P_ij / sum_{k in low_levels} P_ik
for i in range(len(low_levels)):
    suma_P_ik = sum(P_ij[i])
    for j in range(len(low_levels)):
        T_ij[i][j] = P_ij[i][j] / suma_P_ik if suma_P_ik > 0 else 0
print(T_ij)

matriz_secuencias = []
for _ in range(epocs):
    solucion = random.choice([solucion_inicial_2])
    mejor_solucion_temporal = solucion
    best_value_temporal = solucion.objective_value
    low_level_inicial = None
    secuencia = []

    while True:
        # si no hay una low level inicial, se elige una al azar
        if low_level_inicial is None:
            low_level_elegida = random.choice(low_levels)
            id_eleccion = low_level_elegida.id
        else:
            probabilidades_siguiente_low_level = T_ij[low_level_inicial.id - 1,:]
            id_eleccion = seleccionar_segun_probabilidad(probabilidades_siguiente_low_level)
            low_level_elegida = low_levels[id_eleccion]

        secuencia.append(id_eleccion)

 
        solucion_nueva = low_level_elegida.implementacion(solucion)

        if solucion_nueva.is_factible == False: #or solucion_nueva.objective_value <= solucion.objective_value:
            break

        if low_level_inicial is None:
            pass
        else:
            if solucion_nueva.objective_value > best_value_temporal:
                mejor_solucion_temporal = solucion_nueva
                best_value_temporal = solucion_nueva.objective_value
                P_ij[low_level_inicial.id - 1][low_level_elegida.id - 1] += 1

        if low_level_inicial is None:
            id_low_level_inicial = low_level_elegida.id
           # la matriz T_ij se actualiza con el valor de P_ij/ sum_{k in low_levels} P_ik
            suma_P_ik = sum(P_ij[id_low_level_inicial - 1])
            for low_level in low_levels:
                low_level_id = low_level.id
                T_ij[id_low_level_inicial - 1][low_level_id - 1] = P_ij[id_low_level_inicial - 1][low_level_id - 1] / suma_P_ik if suma_P_ik > 0 else 0
            
        low_level_inicial = low_level_elegida
        solucion = solucion_nueva
    
    if best_value_temporal > best_value:
        mejor_solucion = solucion
        best_value = best_value_temporal
        print(f"Nueva mejor solucion encontrada:, Con mejor valor{best_value}, secuencia: {secuencia}")
    matriz_secuencias.append(secuencia)

    #print(T_ij)

print("Mejor solucion final:", mejor_solucion)

[[0.125 0.125 0.125 0.125 0.125 0.125 0.125 0.125]
 [0.125 0.125 0.125 0.125 0.125 0.125 0.125 0.125]
 [0.125 0.125 0.125 0.125 0.125 0.125 0.125 0.125]
 [0.125 0.125 0.125 0.125 0.125 0.125 0.125 0.125]
 [0.125 0.125 0.125 0.125 0.125 0.125 0.125 0.125]
 [0.125 0.125 0.125 0.125 0.125 0.125 0.125 0.125]
 [0.125 0.125 0.125 0.125 0.125 0.125 0.125 0.125]
 [0.125 0.125 0.125 0.125 0.125 0.125 0.125 0.125]]
Nueva mejor solucion encontrada:, Con mejor valor1.0, secuencia: [6]
Mejor solucion final: La solución escoje las ordenes (2, 3) con un total de 2 unidades y los corredores (10, 8) con un valor objetivo de 1.00.


In [22]:
mejor_solucion.is_factible

True

In [40]:
1/soluciones_factibles[0].objective_value+h*soluciones_factibles[0].costo_infactible()

3.1153846153846154

In [38]:
1/soluciones_factibles[-1].objective_value+h*soluciones_factibles[-1].costo_infactible()

2.3636363636363638

In [39]:
1/mejor_solucion.objective_value + h*mejor_solucion.costo_infactible()

940000.014084507

In [28]:
1/mejor_solucion.objective_value + h*mejor_solucion.costo_infactible()

970000.014084507

In [8]:
matriz = np.zeros((3,3))
# ahora rellenamos la matriz con unos


for i in range(matriz.shape[0]):
    for j in range(matriz.shape[1]):
        matriz[i][j] = 1

print(matriz)

print("###########")

print(matriz[0,:])
print("###########")

print(sum(matriz[0]))


[[1. 1. 1.]
 [1. 1. 1.]
 [1. 1. 1.]]
###########
[1. 1. 1.]
###########
3.0
